# Accessing USGS water data using the `dataRetrieval` R package

![](images/data_retrieval.png)

_**Left** Example USGS streamgage setup (Source: [USGS](https://www.usgs.gov/mission-areas/water-resources/science/usgs-national-streamgaging-network))._
_**Right:** Graphic describing the [`dataRetrieval`](https://cran.r-project.org/web/packages/dataRetrieval/vignettes/dataRetrieval.html) R package (Source: [USGS](https://waterdata.usgs.gov/blog/dataretrieval/))._

The primary purpose of this Jupyter notebook is to demonstrate the capabilities for retrieving, processing and visualizing water data from the United States Geological Survey (USGS) in R using the [`dataRetrieval`](https://cran.r-project.org/web/packages/dataRetrieval/vignettes/dataRetrieval.html) package with location-specific examples. The secondary purpose of this notebook is to demonstrate the value of creating computational tools and narratives that can be readily reused by others.

## 1. Setting up workspace for running Jupyter notebook

### 1.1 Install additional packages
When running this notebook in CUAHSI JupyterHub in the JupyterLab interface, there are a few additional packages that must be installed outside of the [list of pre-configured packages](https://drive.google.com/file/d/1hYw0wXlPXAqzbp1tqvw2ZFUDWbX1Cwlo/view).

In [1]:
# suppress warnings
options(warn = -1)
# install packages from CRAN
options(repos = c(CRAN = "https://cloud.r-project.org"))
# list of packages to install
install.packages("plotly")
install.packages("leaflet")
install.packages("dataRetrieval") # need updated version of dataRetrieval
install.packages("rnaturalearth")
install.packages("devtools")
devtools::install_github("ropensci/rnaturalearthhires")

package 'plotly' successfully unpacked and MD5 sums checked

The downloaded binary packages are in
	C:\Users\AbnerBogan\AppData\Local\Temp\RtmpkvzMrC\downloaded_packages
package 'leaflet' successfully unpacked and MD5 sums checked

The downloaded binary packages are in
	C:\Users\AbnerBogan\AppData\Local\Temp\RtmpkvzMrC\downloaded_packages
package 'rnaturalearth' successfully unpacked and MD5 sums checked

The downloaded binary packages are in
	C:\Users\AbnerBogan\AppData\Local\Temp\RtmpkvzMrC\downloaded_packages



Please download and install Rtools 4.4 from https://cran.r-project.org/bin/windows/Rtools/.

Using GitHub PAT from the git credential store.

Skipping install of 'rnaturalearthhires' from a github remote, the SHA1 (e4736f63) has not changed since last install.
  Use `force = TRUE` to force installation



### 1.2 Load packages
We can now load the libraries required to run this notebook. Note that the version of the package (e.g., `1.0.20`) is also referenced to help enable reuse of these materials in other environments.

In [2]:
library(sf)             # (1.0.20) handling and analyzing geospatial data
library(plotly)         # (4.12.0) creating interactive plots and charts
library(leaflet)        # (2.2.3)  building interactive maps
library(tidyverse)      # (2.0.0)  suite of tools for data manipulation
library(dataRetrieval)  # (2.7.22) core package for fetching usgs water data
library(rnaturalearth)  # (1.2.0)  access to global map data for base layers and boundaries

Linking to GEOS 3.13.0, GDAL 3.10.1, PROJ 9.5.1; sf_use_s2() is TRUE

Loading required package: ggplot2


Attaching package: 'plotly'


The following object is masked from 'package:ggplot2':

    last_plot


The following object is masked from 'package:stats':

    filter


The following object is masked from 'package:graphics':

    layout


── Attaching core tidyverse packages ──────────────────────────────────────────────────────────────── tidyverse 2.0.0 ──
✔ dplyr     1.1.4     ✔ readr     2.1.6
✔ forcats   1.0.1     ✔ stringr   1.6.0
✔ lubridate 1.9.4     ✔ tibble    3.3.1
✔ purrr     1.2.1     ✔ tidyr     1.3.2
── Conflicts ────────────────────────────────────────────────────────────────────────────────── tidyverse_conflicts() ──
✖ dplyr::filter() masks plotly::filter(), stats::filter()
✖ dplyr::lag()    masks stats::lag()
ℹ Use the conflicted package (<http://conflicted.r-lib.org/>) to force all conflicts to become errors


## 2. Define inputs for running notebook
This notebook will require a few inputs. First, we will define a nearby landmark and its location.

In [3]:
# define a landmark
input_location <- tibble(
    lon=-76.13,
    lat=43.04,
    label='Syracuse University'
)

We will also want to define the number of nearby USGS gages we would like to investigate.

In [4]:
# define number of sites
input_num_sites <- 5

Next, we can define the time range that we are interested in retrieving water data. 

In [5]:
# define start and end time range in YYYY-MM-DD format
input_time_range_start <- '2025-01-01'
input_time_range_end <- '2026-01-01'

Lastly, we can define which water data value we are interested in retrieving. A list of available parameters and their codes can be found [here](https://api.waterdata.usgs.gov/ogcapi/v0/collections/parameter-codes/items).

In [6]:
# define paramter code (e.g., 00060 = discharge/streamflow)
input_parameter_code = "00060"

## 3. Read in metadata of USGS gage sites

In this section, we will use the `dataRetrieval::read_waterdata_ts_meta` function to return the metadata of USGS gages that have time series data that we are interested in. First, we can use the `sf` package to find which state our landmark is located.

In [7]:
# get state from input
location_info_sf <- sf::st_as_sf(input_location, coords = c("lon", "lat"), crs = 4326) %>%
    sf::st_join(ne_states(country = "united states of america", returnclass = "sf")) %>%
    select(name,postal,label)
print(location_info_sf)

Simple feature collection with 1 feature and 3 fields
Geometry type: POINT
Dimension:     XY
Bounding box:  xmin: -76.13 ymin: 43.04 xmax: -76.13 ymax: 43.04
Geodetic CRS:  WGS 84
# A tibble: 1 × 4
  name     postal label                     geometry
  <chr>    <chr>  <chr>                  <POINT [°]>
1 New York NY     Syracuse University (-76.13 43.04)


Next, we can use the use `dataRetrieval::read_waterdata_ts_meta` function to access the time series metadata. Note that we will return sites in the state of our landmark.

In [8]:
# write flag for checking if the output exists
monitoring_sites_state_streamflow_csv <- paste0('monitoring_sites_',location_info_sf$postal,'_',input_parameter_code,'.csv')
monitoring_sites_state_names_csv <- paste0('monitoring_sites_',location_info_sf$postal,'_','names','.csv')

if (file.exists(monitoring_sites_state_streamflow_csv)) {
    monitoring_sites_state_streamflow <- read_csv(monitoring_sites_state_streamflow_csv)
    monitoring_sites_state_names <- read_csv(monitoring_sites_state_names_csv)
} else {
    # get monitoring locations
    monitoring_sites_state_streamflow <- read_waterdata_ts_meta(
      # filter by state of interest
      state_name     = location_info_sf$name,
      parameter_code = input_parameter_code,
      # filter by statistic
      computation_identifier = 'Mean',  
      computation_period_identifier = 'Daily'
    )
    # Pull names of all sites in state of interest
    monitoring_sites_state_names <- read_waterdata_monitoring_location(
      state_name     = location_info_sf$name,
      properties = c("monitoring_location_id", "monitoring_location_name")
    )
    # write to file 
    write_csv(monitoring_sites_state_streamflow,monitoring_sites_state_streamflow_csv)
    write_csv(monitoring_sites_state_names,monitoring_sites_state_names_csv)
  }

print(monitoring_sites_state_streamflow)

Rows: 697 Columns: 22
── Column specification ────────────────────────────────────────────────────────────────────────────────────────────────
Delimiter: ","
chr  (17): unit_of_measure, parameter_name, parameter_code, statistic_id, hy...
dttm  (5): last_modified, begin, end, begin_utc, end_utc

ℹ Use `spec()` to retrieve the full column specification for this data.
ℹ Specify the column types or set `show_col_types = FALSE` to quiet this message.
Rows: 89568 Columns: 2
── Column specification ────────────────────────────────────────────────────────────────────────────────────────────────
Delimiter: ","
chr (2): monitoring_location_id, monitoring_location_name

ℹ Use `spec()` to retrieve the full column specification for this data.
ℹ Specify the column types or set `show_col_types = FALSE` to quiet this message.


# A tibble: 697 × 22
   unit_of_measure parameter_name parameter_code statistic_id
   <chr>           <chr>          <chr>          <chr>       
 1 ft^3/s          Discharge      00060          00003       
 2 ft^3/s          Discharge      00060          00003       
 3 ft^3/s          Discharge      00060          00003       
 4 ft^3/s          Discharge      00060          00003       
 5 ft^3/s          Discharge      00060          00003       
 6 ft^3/s          Discharge      00060          00003       
 7 ft^3/s          Discharge      00060          00003       
 8 ft^3/s          Discharge      00060          00003       
 9 ft^3/s          Discharge      00060          00003       
10 ft^3/s          Discharge      00060          00003       
# ℹ 687 more rows
# ℹ 18 more variables: hydrologic_unit_code <chr>, state_name <chr>,
#   last_modified <dttm>, begin <dttm>, end <dttm>, begin_utc <dttm>,
#   end_utc <dttm>, computation_period_identifier <chr>,
#   computation_ident

We can then filter out the USGS gage sites with data in the time range of interest and prep the dataframe for visualization.

In [9]:
# get all sites
sites <- monitoring_sites_state_streamflow %>%
  # remove sites with no data in time range
  filter(as.Date(begin)<as.Date(input_time_range_start)) %>%
  filter(as.Date(end)>as.Date(input_time_range_end)) %>%
  # Clean the string geometry
  mutate(clean_coords = str_remove_all(geometry, "c\\(|\\)")) %>%
  # Split coordinates into columns
  separate(clean_coords, into = c("site_lon", "site_lat"), sep = ",\\s*", convert = TRUE) %>%
  # Convert to sf
  st_as_sf(coords = c("site_lon", "site_lat"), crs = 4326) %>%
    # add names back to the table
    left_join(
    monitoring_sites_state_names %>%
      select(monitoring_location_id, monitoring_location_name),
    by = "monitoring_location_id"
  )

print(sites)

Simple feature collection with 300 features and 22 fields
Geometry type: POINT
Dimension:     XY
Bounding box:  xmin: -79.58992 ymin: 40.52542 xmax: -72.68694 ymax: 44.99961
Geodetic CRS:  WGS 84
# A tibble: 300 × 23
   unit_of_measure parameter_name parameter_code statistic_id
   <chr>           <chr>          <chr>          <chr>       
 1 ft^3/s          Discharge      00060          00003       
 2 ft^3/s          Discharge      00060          00003       
 3 ft^3/s          Discharge      00060          00003       
 4 ft^3/s          Discharge      00060          00003       
 5 ft^3/s          Discharge      00060          00003       
 6 ft^3/s          Discharge      00060          00003       
 7 ft^3/s          Discharge      00060          00003       
 8 ft^3/s          Discharge      00060          00003       
 9 ft^3/s          Discharge      00060          00003       
10 ft^3/s          Discharge      00060          00003       
# ℹ 290 more rows
# ℹ 19 more variables

Next, we can use the `sf` package to calculate the distance of each gage site relative to our input landmark and return the nearest sites.

In [10]:
# Add a distance column relative to landmark and return the nearest sites
nearest_sites <- sites %>%
  mutate(distance_meters = st_distance(geometry, location_info_sf)) %>%
  arrange(distance_meters) %>%
  slice_head(n = input_num_sites) %>%
  select(c(monitoring_location_id,monitoring_location_name,geometry,unit_of_measure,parameter_name,begin,end))

print(nearest_sites)

Simple feature collection with 5 features and 6 fields
Geometry type: POINT
Dimension:     XY
Bounding box:  xmin: -76.28711 ymin: 42.98333 xmax: -75.85861 ymax: 43.21117
Geodetic CRS:  WGS 84
# A tibble: 5 × 7
  monitoring_location_id monitoring_location_name                  geometry
  <chr>                  <chr>                                  <POINT [°]>
1 USGS-04240010          ONONDAGA CREEK AT SPENCER ST…   (-76.162 43.05744)
2 USGS-04239000          ONONDAGA CREEK AT DORWIN AVE… (-76.15083 42.98333)
3 USGS-04247000          ONEIDA RIVER NEAR EUCLID NY   (-76.21778 43.20536)
4 USGS-04244000          CHITTENANGO CREEK NEAR CHITT… (-75.85861 43.02308)
5 USGS-04247055          OSWEGO RIVER NEAR PHOENIX NY  (-76.28711 43.21117)
# ℹ 4 more variables: unit_of_measure <chr>, parameter_name <chr>,
#   begin <dttm>, end <dttm>


## 4. Visualize nearby USGS gage sites
We can now take a look at the nearby USGS sites using the `leaflet` library! The map below is interactive and you can zoom and click on each marker to see information about the sites. The input landmark is also plotted in another color for reference.

In [11]:
color_sites <- "blue"
color_landmark <- "red"

# make leaflet map
leaflet() %>%
  addTiles() %>%
  
  # Layer 1: USGS Gages (Blue Circles)
  addCircleMarkers(
    data = nearest_sites,
    color = color_sites,       # Outline color
    fillColor = color_sites,   # Fill color
    fillOpacity = 0.6,
    radius = 6,
    popup = ~paste0(
      "<b>Site ID:</b> ", monitoring_location_id, "<br>",
      "<b>Station Name:</b> ", monitoring_location_name
    )
  ) %>%
  
  # Layer 2: Input Location (Red Circle)
  addCircleMarkers(
    data = location_info_sf,
    color = color_landmark,
    fillColor = color_landmark,
    fillOpacity = 1,      # Solid fill to make it stand out
    radius = 8,           # Slightly larger radius
    popup = ~paste0("<b>Landmark Name:</b> ", label)
  )

HTML widgets cannot be represented in plain text (need html)

## 5. Retrieve USGS water data values
We can now use the `dataRetrieval::read_waterdata_daily` function to retrieve the actual data.

In [12]:
# 1. Initialize an empty list to collect data
data_values_all_sites <- list()

for (i in seq(nrow(nearest_sites))) {
  site_id <- nearest_sites$monitoring_location_id[i]
  site_name <- nearest_sites$monitoring_location_name[i] 
  data_values_csv <- paste0(input_time_range_start, '_', input_time_range_end, '_', site_id, '.csv')
  
  if (file.exists(data_values_csv)) {
    data_values <- read_csv(data_values_csv, show_col_types = FALSE)
  } else {
    data_values <- read_waterdata_daily(
      monitoring_location_id = site_id,
      parameter_code = input_parameter_code,
      statistic_id = "00003",
      time = c(input_time_range_start, input_time_range_end)
    )
    write_csv(data_values, data_values_csv)
  }

  print(data_values)

  # Convert time to Date and add a site label column
  data_values <- data_values %>%
    mutate(
      time = as.Date(time),
      site_id_name = paste0(site_id,': ',site_name)
    )
    
  # Append to list
  data_values_all_sites[[i]] <- data_values
}

# Combine all site data into one dataframe
data_values_all_sites <- bind_rows(data_values_all_sites)

# A tibble: 366 × 11
   monitoring_location_id parameter_code statistic_id time       value
   <chr>                  <chr>          <chr>        <date>     <dbl>
 1 USGS-04240010          00060          00003        2025-01-01   337
 2 USGS-04240010          00060          00003        2025-01-02   378
 3 USGS-04240010          00060          00003        2025-01-03   271
 4 USGS-04240010          00060          00003        2025-01-04   224
 5 USGS-04240010          00060          00003        2025-01-05   196
 6 USGS-04240010          00060          00003        2025-01-06   179
 7 USGS-04240010          00060          00003        2025-01-07   156
 8 USGS-04240010          00060          00003        2025-01-08   155
 9 USGS-04240010          00060          00003        2025-01-09   150
10 USGS-04240010          00060          00003        2025-01-10   151
# ℹ 356 more rows
# ℹ 6 more variables: unit_of_measure <chr>, approval_status <chr>,
#   last_modified <dttm>, qualifier <chr>

## 6. Visualize USGS water data
We are now ready to plot our water data! We will leverage the `plotly` library which generates an interactive graph where you can hover over the plots and and view the values.

In [13]:
parameter_name <- nearest_sites$parameter_name[1]
unit_of_measure <- nearest_sites$unit_of_measure[1]

final_plot <- ggplot(data_values_all_sites, aes(x = time, y = value)) + 
  geom_line(color = "blue", linewidth = 0.6) + 
  # Facet by site_label. 'free_y' is essential for readability
  facet_wrap(~site_id_name, ncol = 1, scales = "free_y") +
  # This removes the 5% padding ggplot adds to the ends of the axes
  scale_x_date(expand = c(0, 0)) + 
  scale_y_continuous(expand = expansion(mult = c(0.1, 0.1))) + # Adds 10% padding top/bottom only
  labs(
    title = paste0(parameter_name, ' comparsion across sites'),
    subtitle = paste("Period:", input_time_range_start, "to", input_time_range_end),
    y = paste0(parameter_name, ' (',unit_of_measure, ')'),
    x = "Date"
  ) +
  theme_minimal() +
  theme(
    strip.text = element_text(face = "bold", size = 9), # Improve facet header readability
    panel.spacing = unit(1, "lines"),                  # Add space between graphs
    axis.text.x = element_text(angle = 0)              # Keep dates horizontal
  )

# add dynamic height adjustment based on number of sites
dynamic_height <- (input_num_sites * 100)

# make an interactive plot using the plotly library
plotly::ggplotly(final_plot, height = dynamic_height)

HTML widgets cannot be represented in plain text (need html)

In [14]:
print(paste0('Last tested: ',Sys.Date()))

[1] "Last tested: 2026-02-05"
